In [1]:
import os
import gc
import json
import numpy as np
import pandas as pd
import torch
from sentence_transformers import SentenceTransformer
import scipy
from sklearn.feature_extraction.text import TfidfVectorizer
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import textstat
from tqdm import tqdm
from typing import Dict, List, Tuple, NamedTuple, Callable, Any
import scml
import mylib

In [2]:
class Conf(NamedTuple):
    device: torch.device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    pretrained_dir: str = "pretrained/"
    data_dir: str = "data/"
    dtfy_model_max_length: int = 512
    dtfy_batch_size: int = 64
    dtfy_models: Dict[str, str] = {
        "dto_": f"{pretrained_dir}unitaryai/detoxify/toxic_original-c1212f89.ckpt",
        "dtu_": f"{pretrained_dir}unitaryai/detoxify/toxic_debiased-c7548aa0.ckpt",
        "dtm_": f"{pretrained_dir}unitaryai/detoxify/multilingual_debiased-0b549669.ckpt"
    }
    dtfy_configs: Dict[str, str] = {
        "dto_": f"{pretrained_dir}bert-base-uncased",
        "dtu_": f"{pretrained_dir}roberta-base",
        "dtm_": f"{pretrained_dir}xlm-roberta-base"
    }
    tweeteval_model_max_length: int = 512
    tweeteval_batch_size: int = 64
    tweeteval_models: Dict[str, str] = {
        "te_roberta_off": f"{pretrained_dir}cardiffnlp/twitter-roberta-base-offensive",
        "te_roberta_emo_anger": f"{pretrained_dir}cardiffnlp/twitter-roberta-base-emotion",
        "te_roberta_snt_neg": f"{pretrained_dir}cardiffnlp/twitter-roberta-base-sentiment",
        "te_roberta_iro": f"{pretrained_dir}cardiffnlp/twitter-roberta-base-irony",
        "te_xlm_roberta_snt_neg": f"{pretrained_dir}cardiffnlp/twitter-xlm-roberta-base-sentiment",
    }
    tweeteval_label_index: Dict[str, int] = {
        "te_roberta_off": 1,
        "te_roberta_emo_anger": 0,
        "te_roberta_snt_neg": 0,
        "te_roberta_iro": 1,
        "te_xlm_roberta_snt_neg": 0,
    }
    hatebert_model_max_length: int = 512
    hatebert_batch_size: int = 128
    hatebert_models: Dict[str, str] = {
        "hb_bert_off": f"{pretrained_dir}hatebert/bert-offenseval",
        "hb_bert_abu" : f"{pretrained_dir}hatebert/bert-abuseval",
        "hb_hatebert_off": f"{pretrained_dir}hatebert/hatebert-offenseval",
        "hb_hatebert_abu" : f"{pretrained_dir}hatebert/hatebert-abuseval",
    }
    vocab_file: str = f"{data_dir}vocab.json"
    vad_file: str = f"{data_dir}vad.tsv"
        
        
conf = Conf()
print(conf)
if conf.device.type == 'cuda':
    for i in range(torch.cuda.device_count()):
        print(f"device={i}, {torch.cuda.get_device_name(i)}")
        print('Mem Allocated:', round(torch.cuda.memory_allocated(i)/1024**3,1), 'GB')
        print('Mem Cached:   ', round(torch.cuda.memory_reserved(i)/1024**3,1), 'GB')

Conf(device=device(type='cuda'), pretrained_dir='pretrained/', data_dir='data/', dtfy_model_max_length=512, dtfy_batch_size=256, dtfy_models={'dto_': 'pretrained/unitaryai/detoxify/toxic_original-c1212f89.ckpt', 'dtu_': 'pretrained/unitaryai/detoxify/toxic_debiased-c7548aa0.ckpt', 'dtm_': 'pretrained/unitaryai/detoxify/multilingual_debiased-0b549669.ckpt'}, dtfy_configs={'dto_': 'pretrained/bert-base-uncased', 'dtu_': 'pretrained/roberta-base', 'dtm_': 'pretrained/xlm-roberta-base'}, tweeteval_model_max_length=512, tweeteval_batch_size=64, tweeteval_models={'te_roberta_off': 'pretrained/cardiffnlp/twitter-roberta-base-offensive', 'te_roberta_emo_anger': 'pretrained/cardiffnlp/twitter-roberta-base-emotion', 'te_roberta_snt_neg': 'pretrained/cardiffnlp/twitter-roberta-base-sentiment', 'te_roberta_iro': 'pretrained/cardiffnlp/twitter-roberta-base-irony', 'te_xlm_roberta_snt_neg': 'pretrained/cardiffnlp/twitter-xlm-roberta-base-sentiment'}, tweeteval_label_index={'te_roberta_off': 1, 'te_r

In [3]:
percentiles=[.01, .05, .1, .2, .3, .4, .5, .6, .7, .8, .9, .95, .99]
os.environ["TOKENIZERS_PARALLELISM"] = "false"
pd.set_option("use_inf_as_na", True)
pd.set_option("max_info_columns", 9999)
pd.set_option("display.max_columns", 9999)
pd.set_option("display.max_rows", 9999)
pd.set_option('max_colwidth', 9999)
tqdm.pandas()

In [4]:
df = pd.read_parquet("input/em_ruddit.parquet")
tmp = pd.read_parquet("input/em_js18.parquet")
#TODO remove!
tmp = tmp[tmp["text1"].str.len() > 20]
df = df.append(tmp, ignore_index=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 191828 entries, 0 to 191827
Data columns (total 391 columns):
 #    Column                        Non-Null Count   Dtype  
---   ------                        --------------   -----  
 0    label                         5710 non-null    float64
 1    bws                           191828 non-null  float32
 2    worker                        191828 non-null  int8   
 3    text                          191828 non-null  object 
 4    text1                         191828 non-null  object 
 5    text2                         191828 non-null  object 
 6    text3                         191828 non-null  object 
 7    paraphrase-MiniLM-L6-v2_0000  191828 non-null  float32
 8    paraphrase-MiniLM-L6-v2_0001  191828 non-null  float32
 9    paraphrase-MiniLM-L6-v2_0002  191828 non-null  float32
 10   paraphrase-MiniLM-L6-v2_0003  191828 non-null  float32
 11   paraphrase-MiniLM-L6-v2_0004  191828 non-null  float32
 12   paraphrase-MiniLM-L6-v2_0005

In [5]:
black = {"label", "bws", "worker", "text", "text1", "text2", "text3"}
em_cols = set(df.columns) - black
em_cols = list(em_cols)
em_cols.sort()

# Character level features

In [6]:
%%time
col = "length"
df[col] = df["text1"].str.len()
df[col] = df[col].astype(np.int16)

Wall time: 122 ms


In [7]:
def digit_frac(row) -> float:
    return mylib.digit_frac(row["text1"])


def letter_frac(row) -> float:
    return mylib.letter_frac(row["text1"])


def space_frac(row) -> float:
    return mylib.space_frac(row["text1"])


def punc_frac(row) -> float:
    return mylib.punc_frac(row["text1"])


def upper_frac(row) -> float:
    return mylib.upper_frac(row["text1"])


def repeat_char_frac(row) -> float:
    return mylib.repeat_char_frac(row["text1"])


def repeat_substring_frac(row) -> float:
    return mylib.repeat_substring_frac(row["text1"])


char_fns: Dict[str, Callable] = {
    "digit_frac": digit_frac,
    "letter_frac": letter_frac,
    "space_frac": space_frac,
    "punc_frac": punc_frac,
    "upper_frac": upper_frac,
    "repeat_char_frac": repeat_char_frac,
    "repeat_substring_frac": repeat_substring_frac,
}

In [8]:
for col, fn in char_fns.items():
    print(col)
    df[col] = df.progress_apply(fn, axis=1)
    df[col] = df[col].astype(np.float32)

digit_frac


100%|████████████████████████████████████| 191828/191828 [00:07<00:00, 25634.83it/s]


letter_frac


100%|████████████████████████████████████| 191828/191828 [00:07<00:00, 25250.07it/s]


space_frac


...

100%|████████████████████████████████████| 191828/191828 [00:07<00:00, 25525.73it/s]


repeat_char_frac


100%|████████████████████████████████████| 191828/191828 [00:11<00:00, 16755.65it/s]


repeat_substring_frac


100%|██████████████████████████████████████| 191828/191828 [04:59<00:00, 641.53it/s]


# Textstat features

In [9]:
def syllable_count(row) -> int:
    return textstat.syllable_count(row["text1"])


def lexicon_count(row) -> int:
    return textstat.lexicon_count(row["text1"])


def sentence_count(row) -> int:
    return textstat.sentence_count(row["text1"])


def syllables_per_word(row) -> float:
    return row["syllable_count"] / (row["lexicon_count"] + 1)


def syllables_per_sent(row) -> float:
    return row["syllable_count"] / (row["sentence_count"] + 1)


def words_per_sent(row) -> float:
    return row["lexicon_count"] / (row["sentence_count"] + 1)


def flesch_reading_ease(row) -> float:
    return textstat.flesch_reading_ease(row["text1"])


def flesch_kincaid_grade(row) -> float:
    return textstat.flesch_kincaid_grade(row["text1"])


def gunning_fog(row) -> float:
    return textstat.gunning_fog(row["text1"])


def smog_index(row) -> float:
    return textstat.smog_index(row["text1"])


def automated_readability_index(row) -> float:
    return textstat.automated_readability_index(row["text1"])


def coleman_liau_index(row) -> float:
    return textstat.coleman_liau_index(row["text1"])


def linsear_write_formula(row) -> float:
    return textstat.linsear_write_formula(row["text1"])


def dale_chall_readability_score(row) -> float:
    return textstat.dale_chall_readability_score(row["text1"])


preprocess_fns: List[Tuple[str, Callable, Any]] = [
    ("syllable_count", syllable_count, np.int32),
    ("lexicon_count", lexicon_count, np.int32),
    ("sentence_count", sentence_count, np.int32),
]
textstat_fns: List[Tuple[str, Callable, Any]] = [
    ("syllables_per_word", syllables_per_word, np.float32),
    ("syllables_per_sent", syllables_per_sent, np.float32),
    ("words_per_sent", words_per_sent, np.float32),
    ("flesch_reading_ease", flesch_reading_ease, np.float32),
    ("flesch_kincaid_grade", flesch_kincaid_grade, np.float32),
    ("gunning_fog", gunning_fog, np.float32),
    ("smog_index", smog_index, np.float32),
    ("automated_readability_index", automated_readability_index, np.float32),
    ("coleman_liau_index", coleman_liau_index, np.float32),
    ("linsear_write_formula", linsear_write_formula, np.float32),
    ("dale_chall_readability_score", dale_chall_readability_score, np.float32),
]

In [10]:
for col, fn, dtype in preprocess_fns:
    print(col)
    df[col] = df.progress_apply(fn, axis=1)
    df[col] = df[col].astype(dtype)
for col, fn, dtype in textstat_fns:
    print(col)
    df[col] = df.progress_apply(fn, axis=1)
    df[col] = df[col].astype(dtype)

syllable_count


100%|█████████████████████████████████████| 191828/191828 [00:20<00:00, 9261.68it/s]


lexicon_count


100%|████████████████████████████████████| 191828/191828 [00:05<00:00, 36311.75it/s]


sentence_count


...

100%|████████████████████████████████████| 191828/191828 [00:11<00:00, 17370.82it/s]


linsear_write_formula


100%|█████████████████████████████████████| 191828/191828 [00:22<00:00, 8592.52it/s]


dale_chall_readability_score


100%|█████████████████████████████████████| 191828/191828 [00:24<00:00, 7691.96it/s]


# VAD lexicon
- only using Valence and Arousal scores

In [11]:
vad_df = pd.read_csv(conf.vad_file, header=0, names=["term", "valence", "arousal", "dominance"], 
                 sep="\t", engine="c", low_memory=False)
cols = ["valence", "arousal", "dominance"]
vad_df[cols] = vad_df[cols].astype(np.float16)
vad_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19970 entries, 0 to 19969
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   term       19969 non-null  object 
 1   valence    19970 non-null  float16
 2   arousal    19970 non-null  float16
 3   dominance  19970 non-null  float16
dtypes: float16(3), object(1)
memory usage: 273.2+ KB


In [12]:
valence: Dict[str, float] = {}
arousal: Dict[str, float] = {}
for t in tqdm(vad_df.itertuples()):
    v = getattr(t, "valence")
    a = getattr(t, "arousal")
    term = str(getattr(t, "term")).strip().lower()
    if v < 0.25:
        valence[term] = v
    if a > 0.75:
        arousal[term] = a
print(f"len(valence)={len(valence)}, len(arousal)={len(arousal)}")

19970it [00:00, 586848.16it/s]

len(valence)=3011, len(arousal)=1944


In [13]:
vad_fs = ["valence_min", "valence_max", "valence_mean", "arousal_min", "arousal_max", "arousal_mean"]
rows = []
for text in tqdm(df["text3"]):
    vs = []
    ars = []
    tokens = text.split()
    for t in tokens:
        if t in valence:
            vs.append(valence[t])
        if t in arousal:
            ars.append(arousal[t])
    if len(vs) == 0:
        vs = [-1]
    if len(ars) == 0:
        ars = [-1]
    row = [min(vs), max(vs), np.mean(vs), min(ars), max(ars), np.mean(ars)]
    rows.append(row)
df[vad_fs] = rows
df[vad_fs] = df[vad_fs].astype(np.float32)
del rows, valence, arousal, vad_df
gc.collect()

100%|████████████████████████████████████| 191828/191828 [00:06<00:00, 31073.87it/s]


0

# TF-IDF features

In [14]:
vocabulary, idf = [], []
with open(conf.vocab_file) as f:
    tmp = json.load(f)
    vocabulary = tmp["term"]
    idf = tmp["idf"]
print(f"len(vocab)={len(vocabulary)}\n{vocabulary}")
assert len(vocabulary) == len(idf)

len(vocab)=4098
['abandon', 'abandonment', 'abash', 'abduct', 'abduction', 'aberrant', 'aberration', 'abhor', 'abhorrence', 'abhorrent', 'ablaze', 'abnormal', 'abnormality', 'abominable', 'abominate', 'abomination', 'abort', 'abortion', 'abortive', 'abrupt', 'abruptly', 'abscess', 'absence', 'absent', 'absentee', 'absurd', 'absurdity', 'abuse', 'abusive', 'accelerant', 'accelerate', 'acceleration', 'accelerator', 'accident', 'accidental', 'acclaim', 'accurse', 'accusation', 'accusative', 'accuse', 'accuser', 'ache', 'achievement', 'achy', 'acidity', 'acne', 'acrobat', 'action', 'action figure', 'activation', 'addict', 'addicted', 'addiction', 'adrenalin', 'adrenaline', 'adulterate', 'adulterer', 'adultery', 'adventure', 'adventurer', 'adventurous', 'adversary', 'adversity', 'aerobic', 'afire', 'afraid', 'african', 'african american', 'age', 'aged', 'agglomeration', 'aggravate', 'aggravating', 'aggravation', 'aggresive', 'aggression', 'aggressive', 'aggressively', 'aggressiveness', 'agg

In [15]:
%%time
vec = TfidfVectorizer(vocabulary=vocabulary, ngram_range=(1, 3), analyzer="word")
vec.idf_ = idf
x = vec.transform(df["text3"])
print(f"x.shape={x.shape}\n{x[0]}")
ti_features = []
for t in vocabulary:
    words = ["ti"] + t.split()
    ti_features.append("_".join(words))
df[ti_features] = scipy.sparse.csr_matrix(x).todense()
print("cast float32")
for col in tqdm(ti_features):
    df[col] = df[col].astype(np.float32)
df = df.copy()  # defragment

x.shape=(191828, 4098)
  (0, 4046)	0.7331980323751862
  (0, 2339)	0.6800151802137622


s:\dev\seahrh\kaggle-jigsaw-toxic-severity-rating\env\lib\site-packages\pandas\core\frame.py:3673: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  self[col] = igetitem(value, i)


Wall time: 30.9 s


# TweetEval labels

In [16]:
sentences = list(df["text2"])
for col, model_dir in conf.tweeteval_models.items():
    tokenizer = AutoTokenizer.from_pretrained(
        model_dir, 
        model_max_length=conf.tweeteval_model_max_length
    )
    #print(f"{repr(tokenizer)}\nmodel_input_names={tokenizer.model_input_names}")
    x = tokenizer(sentences, truncation=True, padding="max_length")
    batches = torch.utils.data.DataLoader(mylib.Dataset(x), batch_size=conf.tweeteval_batch_size, shuffle=False)
    model = AutoModelForSequenceClassification.from_pretrained(model_dir)
    model.eval()
    model.to(conf.device)
    logits = None
    with torch.no_grad():
        for batch in tqdm(batches):
            for k, v in batch.items():
                batch[k] = v.to(conf.device)
            outputs = model(**batch)
            tmp = outputs.logits.detach().cpu()
            if logits is None:
                logits = tmp
            else:
                logits = torch.cat((logits, tmp), 0)
    logits = torch.nn.functional.softmax(logits, dim=1)
    print(f"{col} {logits.size()}\nlogits[:10]={logits[:10]}")
    df[col] = logits[:,conf.tweeteval_label_index[col]]
    df[col] = df[col].astype(np.float32)
    del tokenizer, model
    gc.collect()

100%|█████████████████████████████████████████| 2998/2998 [2:16:57<00:00,  2.74s/it]
s:\dev\seahrh\kaggle-jigsaw-toxic-severity-rating\env\lib\site-packages\ipykernel_launcher.py:26: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`


te_roberta_off torch.Size([191828, 2])
logits[:10]=tensor([[0.9025, 0.0975],
        [0.5804, 0.4196],
        [0.6679, 0.3321],
        [0.8045, 0.1955],
        [0.7880, 0.2120],
        [0.7823, 0.2177],
        [0.8272, 0.1728],
        [0.6837, 0.3163],
        [0.7598, 0.2402],
        [0.9035, 0.0965]])


100%|█████████████████████████████████████████| 2998/2998 [2:17:05<00:00,  2.74s/it]


te_roberta_emo_anger torch.Size([191828, 4])
logits[:10]=tensor([[0.0376, 0.0565, 0.8628, 0.0431],
        [0.1369, 0.1012, 0.2558, 0.5061],
        [0.8166, 0.0105, 0.0391, 0.1338],
        [0.9419, 0.0041, 0.0231, 0.0308],
        [0.6684, 0.0184, 0.1338, 0.1794],
        [0.8703, 0.0090, 0.0602, 0.0605],
        [0.8556, 0.0071, 0.0948, 0.0425],
        [0.8475, 0.0155, 0.0260, 0.1111],
        [0.8054, 0.0086, 0.0704, 0.1156],
        [0.1417, 0.3192, 0.3703, 0.1687]])


100%|█████████████████████████████████████████| 2998/2998 [2:17:22<00:00,  2.75s/it]


te_roberta_snt_neg torch.Size([191828, 3])
logits[:10]=tensor([[0.0407, 0.7561, 0.2032],
        [0.4268, 0.5488, 0.0244],
        [0.7662, 0.2259, 0.0080],
        [0.6066, 0.3729, 0.0206],
        [0.5111, 0.4282, 0.0607],
        [0.5525, 0.4095, 0.0379],
        [0.3226, 0.6394, 0.0380],
        [0.7787, 0.2147, 0.0066],
        [0.7998, 0.1863, 0.0139],
        [0.1055, 0.6091, 0.2854]])


100%|█████████████████████████████████████████| 2998/2998 [2:17:20<00:00,  2.75s/it]


te_roberta_iro torch.Size([191828, 2])
logits[:10]=tensor([[0.7999, 0.2001],
        [0.4219, 0.5781],
        [0.3392, 0.6608],
        [0.8240, 0.1760],
        [0.8902, 0.1098],
        [0.6376, 0.3624],
        [0.7453, 0.2547],
        [0.0874, 0.9126],
        [0.8681, 0.1319],
        [0.6555, 0.3445]])


100%|█████████████████████████████████████████| 2998/2998 [2:17:33<00:00,  2.75s/it]


te_xlm_roberta_snt_neg torch.Size([191828, 3])
logits[:10]=tensor([[0.1049, 0.7652, 0.1299],
        [0.1865, 0.7562, 0.0573],
        [0.4178, 0.4738, 0.1084],
        [0.7074, 0.2630, 0.0296],
        [0.7878, 0.1841, 0.0281],
        [0.5432, 0.4069, 0.0500],
        [0.5321, 0.4271, 0.0408],
        [0.5248, 0.4357, 0.0396],
        [0.9013, 0.0858, 0.0129],
        [0.3988, 0.4830, 0.1182]])


# HateBert labels

In [17]:
# all Hatebert models use the same tokenizer
tokenizer = AutoTokenizer.from_pretrained(
    conf.hatebert_models["hb_hatebert_off"], 
    model_max_length=conf.hatebert_model_max_length
)
print(f"{repr(tokenizer)}\nmodel_input_names={tokenizer.model_input_names}")

PreTrainedTokenizerFast(name_or_path='pretrained/hatebert/hatebert-offenseval', vocab_size=30522, model_max_len=512, is_fast=True, padding_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'})
model_input_names=['input_ids', 'token_type_ids', 'attention_mask']


In [18]:
%%time
x = tokenizer(sentences, truncation=True, padding="max_length")
print(f"{repr(x.keys())}\nlen={len(x['input_ids'])}")

dict_keys(['input_ids', 'token_type_ids', 'attention_mask'])
len=191828
Wall time: 1min 54s


In [19]:
batches = torch.utils.data.DataLoader(mylib.Dataset(x), batch_size=conf.hatebert_batch_size, shuffle=False)
for col, model_dir in conf.hatebert_models.items():    
    model = AutoModelForSequenceClassification.from_pretrained(model_dir)
    model.eval()
    model.to(conf.device)
    logits = None
    with torch.no_grad():
        for batch in tqdm(batches):
            for k, v in batch.items():
                batch[k] = v.to(conf.device)
            outputs = model(**batch)
            tmp = outputs.logits.detach().cpu()
            if logits is None:
                logits = tmp
            else:
                logits = torch.cat((logits, tmp), 0)
    logits = torch.nn.functional.softmax(logits, dim=1)
    print(f"{col} {logits.size()}\nlogits[:10]={logits[:10]}")
    df[col] = logits[:,1]
    df[col] = df[col].astype(np.float32)

100%|█████████████████████████████████████████| 1499/1499 [2:19:13<00:00,  5.57s/it]
s:\dev\seahrh\kaggle-jigsaw-toxic-severity-rating\env\lib\site-packages\ipykernel_launcher.py:19: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`


hb_bert_off torch.Size([191828, 2])
logits[:10]=tensor([[0.9598, 0.0402],
        [0.7718, 0.2282],
        [0.7567, 0.2433],
        [0.9064, 0.0936],
        [0.8318, 0.1682],
        [0.7811, 0.2189],
        [0.5952, 0.4048],
        [0.8502, 0.1498],
        [0.7770, 0.2230],
        [0.9258, 0.0742]])


100%|█████████████████████████████████████████| 1499/1499 [2:19:56<00:00,  5.60s/it]


hb_bert_abu torch.Size([191828, 2])
logits[:10]=tensor([[0.9910, 0.0090],
        [0.9717, 0.0283],
        [0.9545, 0.0455],
        [0.9631, 0.0369],
        [0.9714, 0.0286],
        [0.8686, 0.1314],
        [0.9001, 0.0999],
        [0.8544, 0.1456],
        [0.8708, 0.1292],
        [0.9881, 0.0119]])


100%|█████████████████████████████████████████| 1499/1499 [2:22:12<00:00,  5.69s/it]


hb_hatebert_off torch.Size([191828, 2])
logits[:10]=tensor([[0.9377, 0.0623],
        [0.5526, 0.4474],
        [0.7553, 0.2447],
        [0.7828, 0.2172],
        [0.8787, 0.1213],
        [0.9267, 0.0733],
        [0.8304, 0.1696],
        [0.7886, 0.2114],
        [0.8038, 0.1962],
        [0.8965, 0.1035]])


100%|█████████████████████████████████████████| 1499/1499 [2:19:09<00:00,  5.57s/it]

hb_hatebert_abu torch.Size([191828, 2])
logits[:10]=tensor([[0.9846, 0.0154],
        [0.9717, 0.0283],
        [0.9570, 0.0430],
        [0.9699, 0.0301],
        [0.9698, 0.0302],
        [0.9780, 0.0220],
        [0.9800, 0.0200],
        [0.9733, 0.0267],
        [0.9407, 0.0593],
        [0.9795, 0.0205]])


# Detoxify labels

In [27]:
del logits, tmp
torch.cuda.empty_cache()
gc.collect()

5564

In [28]:
dtfy_fs = []
for prefix, checkpoint in tqdm(conf.dtfy_models.items()):
    res = mylib.detoxify_labels(
        sentences,
        checkpoint=checkpoint,
        config_dir=conf.dtfy_configs[prefix],
        model_max_length=conf.dtfy_model_max_length,
        device=conf.device,
        #batch_size=conf.dtfy_batch_size,
        batch_size=64,
    )
    for k, v in res.items():
        col = prefix + k
        df[col] = v
        df[col] = df[col].astype(np.float32)
        dtfy_fs.append(col)
    torch.cuda.empty_cache()
    gc.collect()

  0%|                                                         | 0/3 [00:00<?, ?it/s]s:\dev\seahrh\kaggle-jigsaw-toxic-severity-rating\env\lib\site-packages\ipykernel_launcher.py:14: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`
  
100%|█████████████████████████████████████████████| 3/3 [1:34:49<00:00, 1896.60s/it]


In [29]:
print(dtfy_fs)

['dto_toxicity', 'dto_severe_toxicity', 'dto_obscene', 'dto_threat', 'dto_insult', 'dto_identity_attack', 'dtu_toxicity', 'dtu_severe_toxicity', 'dtu_obscene', 'dtu_identity_attack', 'dtu_insult', 'dtu_threat', 'dtu_sexual_explicit', 'dtm_toxicity', 'dtm_severe_toxicity', 'dtm_obscene', 'dtm_identity_attack', 'dtm_insult', 'dtm_threat', 'dtm_sexual_explicit']


# Review data

In [30]:
cols = ["bws", "worker", "length"]
cols += list(char_fns.keys())
cols += [x[0] for x in textstat_fns]
cols += dtfy_fs
cols += list(conf.hatebert_models.keys()) 
cols += list(conf.tweeteval_models.keys()) 
cols += vad_fs
cols += ti_features
df[cols].describe(percentiles=percentiles)

bws         worker         length     digit_frac  \
count  191828.000000  191828.000000  191828.000000  191828.000000   
mean       -0.025554      12.121734     215.551463       0.006335   
std         0.137211       7.138316     115.548964       0.019403   
min        -0.889000       0.000000      14.000000       0.000000   
1%         -0.319940       0.000000      59.000000       0.000000   
5%         -0.221003       1.000000      77.000000       0.000000   
10%        -0.175615       2.000000      87.000000       0.000000   
20%        -0.125782       5.000000     108.000000       0.000000   
30%        -0.092675       7.000000     132.000000       0.000000   
40%        -0.065431      10.000000     157.000000       0.000000   
50%        -0.039512      12.000000     188.000000       0.000000   
60%        -0.011233      15.000000     225.000000       0.000000   
70%         0.021831      17.000000     269.000000       0.000000   
80%         0.068575      20.000000     323.000000       0.004598   
90%         0.146142      22.000000     393.000000       0.021053   
95%         0.218182      23.000000     441.000000       0.039683   
99%         0.375842      24.000000     487.000000       0.092593   
max         0.979000      24.000000    1062.000000       0.877378   

         letter_frac     space_frac      punc_frac     upper_frac  \
count  191828.000000  191828.000000  191828.000000  191828.000000   
mean        0.771928       0.172777       0.048960       0.046373   
std         0.047134       0.021058       0.038067       0.081895   
min         0.000000       0.000000       0.000000       0.000000   
1%          0.618182       0.111111       0.000000       0.000000   
5%          0.696764       0.140845       0.013699       0.008197   
10%         0.723913       0.149826       0.018987       0.012195   
20%         0.747899       0.158845       0.025316       0.017910   
30%         0.761364       0.164678       0.030612       0.022472   
40%         0.771208       0.169399       0.035971       0.026667   
50%         0.779503       0.173745       0.041463       0.031250   
60%         0.787081       0.178010       0.047619       0.036496   
70%         0.794643       0.182540       0.055215       0.042918   
80%         0.802920       0.188034       0.065990       0.052632   
90%         0.814024       0.195804       0.084337       0.071429   
95%         0.823529       0.202532       0.104839       0.097744   
99%         0.844073       0.217949       0.173316       0.589931   
max         1.000000       0.493671       1.000000       0.997859   

       repeat_char_frac  repeat_substring_frac  syllables_per_word  \
count     191828.000000          191828.000000       191828.000000   
mean           0.024418               0.006848            1.424079   
std            0.035233               0.042557            0.598037   
min            0.000000               0.000000            0.000000   
1%             0.000000               0.000000            1.034483   
5%             0.000000               0.000000            1.130435   
10%            0.006734               0.000000            1.187500   
20%            0.010554               0.000000            1.250000   
30%            0.013629               0.000000            1.304348   
40%            0.016807               0.000000            1.347826   
50%            0.019912               0.000000            1.389830   
60%            0.023196               0.000000            1.434783   
70%            0.026906               0.000000            1.484848   
80%            0.032258               0.000000            1.549020   
90%            0.041322               0.013844            1.653061   
95%            0.052083               0.024793            1.760000   
99%            0.098361               0.113061            2.096774   
max            0.993576               0.982869          155.500000   

       syllables_per_sent  words_per_sent  flesch_reading_ease

In [ ]:
cols += em_cols
df[cols].info()

In [ ]:
%%time
df[cols].to_parquet("output/tra.parquet", index=False)